# Crease Detection in Trimesh

This Jupyter notebook demonstrates how to detect and visualize crease edges (sharp edges) in a mesh using the `trimesh` and `pyrender` libraries.

In [6]:
import trimesh
import numpy as np

# ─── User Options ─────────────────────────────────────────────────────────────
# Show the original textured mesh?  If False, you'll see only the black creases.
show_mesh = False

# Freestyle‐style crease threshold in degrees
threshold_degrees = 15
angle_thresh      = np.deg2rad(threshold_degrees)
# ────────────────────────────────────────────────────────────────────────────────

# 1. Load your OBJ (textured!) without auto‐processing
loaded = trimesh.load(
    '/home/jeans/progressive_img2sketch/resources/LOD_data_50/0/lod3.obj',
    process=False
)

# 2. Gather the textured Trimesh instances
if isinstance(loaded, trimesh.Scene):
    textured_meshes = list(loaded.geometry.values())
else:
    textured_meshes = [loaded]

# 3. Make an empty Scene (we’ll add only what we want)
scene = trimesh.Scene()

# 4. Optionally add the original meshes
if show_mesh:
    for mesh in textured_meshes:
        scene.add_geometry(mesh)

# 5. For each textured mesh, compute and overlay its creases
for textured in textured_meshes:
    # Build a “clean” copy for adjacency (welds vertices, merges dups)
    clean = trimesh.Trimesh(
        vertices = textured.vertices.copy(),
        faces    = textured.faces.copy(),
        process  = True
    )
    # Compute face‐normal angles
    face_angles = clean.face_adjacency_angles  # θ = arccos(n₁·n₂)
    mask        = face_angles > angle_thresh  # pick normals differing by > threshold
    if not mask.any():
        continue

    # Extract the sharp edges and build segments
    edges    = clean.face_adjacency_edges[mask]  # (k,2)
    segments = clean.vertices[edges]             # (k,2,3)

    # Create a Path3D of those segments
    crease = trimesh.load_path(segments)
    # Color each line segment entity black (RGBA)
    black  = [0, 0, 0, 255]
    crease.colors = np.tile(black, (len(crease.entities), 1))

    scene.add_geometry(crease)

# 6. Finally, show the scene (mesh optional, creases always)
scene.show()


### nigk

In [ ]:

# # 1. Load your OBJ (textured!) without processing
# loaded = trimesh.load(
#     '/home/jeans/progressive_img2sketch/resources/LOD_data_50/1/lod3.obj',
#     process=False
# )

# # 2. Build a scene from what you got (Scene or single Trimesh)
# if isinstance(loaded, trimesh.Scene):
#     scene  = loaded.copy()  
#     meshes = list(scene.geometry.items())  # list of (name, Trimesh)
# else:
#     scene  = trimesh.Scene([loaded])
#     meshes = [('mesh', loaded)]

# # 3. Freestyle Crease threshold
# threshold_degrees = 30.0
# angle_thresh     = np.deg2rad(threshold_degrees)

# for name, textured in meshes:
#     # 4. Make a clean, “just-geometry” copy for adjacency
#     clean = trimesh.Trimesh(
#         vertices = textured.vertices.copy(),
#         faces    = textured.faces.copy(),
#         process  = True       # weld vertices, merge duplicates, compute normals
#     )

#     # 5. Compute the face‐normal angles (0…π), pick > threshold
#     face_angles = clean.face_adjacency_angles               # arccos(n1·n2)
#     mask        = face_angles > angle_thresh                # e.g. > 30°
#     if not mask.any():
#         continue

#     # 6. Gather those edges and build segments
#     edges    = clean.face_adjacency_edges[mask]             # (k,2)
#     segments = clean.vertices[edges]                        # (k,2,3)

#     # 7. Build a Path3D & color each entity black
#     crease = trimesh.load_path(segments)
#     black  = [0,0,0,255]
#     crease.colors = np.tile(black, (len(crease.entities), 1))

#     # 8. Overlay onto the original mesh
#     scene.add_geometry(crease)

# # 9. Show: your textured faces stay perfectly mapped,
# #    and you get crisp black crease lines exactly where you want them.
# scene.show()
